In [1]:
import numpy as np
import numpy.matlib as matlib
import pandas as pd
import scipy as sp
import matplotlib.pyplot as plt
import matplotlib.patches as patches
import matplotlib.colors as mcolors 
from matplotlib import cm
import time

from mpl_toolkits.mplot3d import Axes3D
import plotly.graph_objects as go

import Tabesh2013functions as tb
import aux_tools as aux

mina_cp = pd.read_csv('mina_clusterizada.csv')
z_sorted = np.sort(mina_cp['z'].unique())[::-1]
bancos = np.array(range(1,len(z_sorted)+1))
z_to_banco = dict(zip(z_sorted, bancos))
mina_cp["banco"] = mina_cp["z"].map(z_to_banco)

num_fases = mina_cp['fase'].unique()

fases_new = []
for f in num_fases:
    fase = mina_cp[mina_cp['fase']==f].copy()
    z_sorted = np.sort(fase['z'].unique())[::-1]
    bancos = np.array(range(1,len(z_sorted)+1))
    z_to_banco = dict(zip(z_sorted, bancos))
    fase['banco'] = fase['z'].map(z_to_banco)
    fases_new.append(fase)

mina = pd.concat(fases_new)


R = 0.9
P = 4
cm = 2
cp = 10
cr = 0.25
alpha_ley_corte = 0

BlockWidth=10
BlockHeight=10
BlockHeightZ=16

FTL = 2204.62
ley_marginal = cp/((P-cr)*FTL*R)
ley_critica = (cp+cm)/((P-cr)*FTL*R)

ley_corte = ((1-alpha_ley_corte)*ley_marginal + alpha_ley_corte*(ley_critica))*100

mina_rellena = pd.read_csv('mina_rellena.csv')
mina_rellena = mina_rellena.drop(columns='Unnamed: 0')

In [2]:
params_cono = np.load('params_cono_vol.npy')

Min_Area = 300000

ancho_rampa = 4*BlockWidth

params_cono = list(np.load('params_cono_vol.npy'))
Rampa = tb.Rampa(mina, Cone=list(params_cono), z_min=tb.Z_min(mina, params_cono, Minimum_Area=Min_Area), n=1000, theta_0=-90)
# Puntos_Iniciales = tb.Puntos_Iniciales(mina, Rampa, tb.Z_min(mina, params_cono, Minimum_Area=Min_Area))
id_in_rampa=tb.isin_rampa(mina_rellena, Rampa, 40)

params_cono.append(mina['z'].max())


blocks_in_rampa = mina_rellena[mina_rellena['id'].isin(id_in_rampa)]
block_coords = list(blocks_in_rampa[['x','y','z']].__array__())
all_precedences = tb.all_precedences(mina_rellena, block_coords, 10, 10, 16, config='9-points', angulo_apertura=45)
# precedences = mina_rellena[mina_rellena['id'].isin(all_prec)]

total_ids = set(mina['id'])
total_ids.update(all_precedences)

mina_con_rampa = mina_rellena[mina_rellena['id'].isin(total_ids)]

In [3]:
tb.plot_fase_3D(mina_con_rampa, column_hue='tipomineral')